# Forest harvest scheduling with Model II linear programming formulation: a Gurobi Python implementation

##### Pablo Yapura (ypf@agro.unlp.edu.ar)
##### Facultad de Ciencias Agrarias y Forestales
##### Universidad Nacional de La Plata

## Introduction

Probably the most important instrument for realizing forest management planning is a document known as a harvest schedule or a cutting schedule (Clutter et al., 1983). In spite of these denominations, which emphasize the central role of harvests or tree-cuttings (as in thinnings), a well-conceived schedule should detail all kinds of silvicultural interventions, namely, site preparation, regeneration planting, weeding, fertilization, etc., as well as harvest and thinning. Then, if the whole forest is divided into mutually exclusive stands that are going to be prescribed with the same set of silvicultural treatments all over the planning horizon, the harvest schedule should detail in a timetable the moment during the plan when each of these silvicultural interventions must happen.

In the process of developing the harvest schedule, forest management objectives should be accomplished while ensuring important attributes or outcomes of the plan are satisfied. From a financial standpoint, the objective can usually be expressed as maximizing the present value of future net revenues from the forest. Typical important attributes or outcomes that constrain objective attainments are annual area or volume harvest regulations, cash flow stability, or age-class distribution of the forest at the end of the planning horizon, among others. As it is well known, this problem can be elegantly expressed as an optimization problem, or more precisely, as a linear programming problem. After a comprehensive review, Johnson & Scheurman (1977) elicited two synthetic and conceptual approaches for modeling harvest scheduling as linear programs and coined the Model I and Model II imperishable nomenclatures.

In both models, the initial representation of the forest can be construed in much the same way. In the most detailed end of a plausible continuum, the forest can be divided into true stands that hold the spatial identity as a key attribute. On the less detailed end, the forest can be divided into commonly termed cutting units, which aggregate true stands into larger units in order to control the number of mutually exclusive areas in which the forest is divided, normally at the expense of sacrificing spatial identity. But then, as long as both models define their decision variables in a unique, special way, important differences arise.

In Model I formulations, decision variables are defined for each combination of all the management regimes identified for all the initial subdivisions of the forest. The management regime is a landmark in the formulation of Model I and can be defined as the complete specification of silvicultural interventions to be implemented in the initial subdivision of the forest throughout the whole planning horizon. As the set of complete specifications can be large, especially for long planning horizons, it is understandable the concern of Model I formulations for the number of initial divisions of the forest. More importantly, a consequence of this approach is that the formulation preserves the identity of the initial division of the forest throughout the whole planning horizon.

In Model II formulations, decision variables are defined for each harvest opportunity, and the identity of initial divisions of the forest is lost as soon as the first harvest happens. So, Clutter et al. (1983) use initial strata as designations for initial divisions of the forests instead of cutting units. They also suggest that most Model II formulations compose these strata with age classes in existence at the beginning of the planning horizon. Then, every combination of initial strata with all feasible harvest opportunities, typically expressed as different harvest ages, is represented by one decision variable. After that, upon every harvest opportunity and disregarding the initial strata where they come from, all harvested areas in the same period are collapsed into one particular combination of regeneration periods and subsequent feasible harvest periods and are represented by different decision variables. It is worth noting that it is here that the identity of the initial strata gets lost. Not harvesting can be treated as a special kind of harvest opportunity and so be represented by their own decision variables resulting from the combinations with initial strata or regeneration periods. As can be easily inferred, the Model II approach heavily emphasizes the next rotation only instead of the whole planning period, as was the case with Model I. This focus on only one rotation at a time, combined with long planning horizons, tends to keep the number of variables in the Model II approach at a reasonable number, but this characteristic is problem-specific. Consequently, neither Model I nor Model II results inherently in a more compact formulation, *i.e.*, with fewer decision variables.

In this notebook, a Gurobi Python implementation of the Model II approach will be presented using the same example problem published in Clutter et al. (1983, Chapter 10) and already implemented for the Model I formulation in a separated notebook (Yapura, 2024). Again, Clutter et al. (1983) presentation of harvest scheduling Model II will be closely followed, specially in the mathematical notation. Finally, although this notebook is almost entirely autonomous of the Model I notebook, it is highly likely that some parts will be more understandable after reviewing that notebook (Yapura, 2024).

---
## Problem description

For the sake of completeness, here we reproduce exactly the same presentation of the example problem made in the Model I notebook (Yapura, 2024).

According to Clutter et al. (1983), the example problem is small in the number of variables and constraints but realistic enough to showcase the calculations involved. Literally, the authors present this scenario:

> *Behemoth Pulp Company has just completed construction of a 10,000 ton/day pulp mill. However, Behemoth owns no land in the vicinity of this mill, and the supply of raw material to the mill is considered to be a matter of some concern. Since the XYZ Timber Co. owns 155,000 acres nearby, Behemoth has agreed to buy wood from XYZ. The contract requires XYZ to provide at least 500,000 cunits per year for harvest by Behemoth in each of the next 16 years. The agreed-on stumpage price is $25 per cunit. If XYZ wishes to provide more than 500,000 cunits in any year, Behemoth will purchase the additional wood at the same price.*

XYZ forest management unit is composed of 90,000 acres of 13-year-old plantations and 65,000 acres of non-planted brushlands that can be used for timber production. Regeneration costs are \\$150 per acre in both land types, and constant annual tax and administrative costs are \\$1.50 per acre. The forest company uses an interest rate of 5 percent for financial analysis. Both planted stands and subsequent plantations follow the same yield table:

| Age (years) | Yield (cunits/acre) || Age (years) | Yield (cunits/acre) || Age (years) | Yield (cunits/acre) |
| --- | --- || --- |--- || --- | --- |
| 10 | 29.10 || 17 | 65.96 || 24 | 90.24 |
| 11 | 34.98 || 18 | 70.20 || 25 | 92.75 |
| 12 | 40.80 || 19 | 73.91 || 26 | 94.90 |
| 13 | 46.67 || 20 | 77.60 || 27 | 96.93 |
| 14 | 52.22 || 21 | 81.06 || 28 | 98.56 |
| 15 | 57.00 || 22 | 84.26 || 29 | 100.05 |
| 16 | 61.60 || 23 | 87.40 || 30 | 100.80 |

The problem that XYZ Company has to solve is to find the schedule of harvest and regeneration that maximizes the present value of all future net incomes while providing the half million cunits in each of the next 16 years they have committed to Behemoth.

---
## Model formulation

In developing the mathematical model, the time representation will be the same as used in the Model I formulation. Accordingly, the 16-year-long agreement is the planning horizon and is divided into 8 cutting periods of 2 years. Also in place is the specification of a minimum harvest age of 10 years (*i.e.*, 5 cutting periods).

To better understand the process of decision variable identification, perhaps it is helpful to consider a management regime for the Model I 13-year-old cutting unit that represents a pattern of harvest and plant in period 2, followed by a harvest and plant in period 7, and the existence of planted stands aged 3 years old at the end of the plan horizon. Like all regimes in the Model I formulation, this management regime is represented by one single decision variable, as it specifies what to do throughout the whole planning horizon. Instead, three decision variables will be necessary to describe this particular pattern in the Model II formulation: one for the harvest of the existing stand at the beginning of the planning horizon, another for the regeneration in period 2 and harvest in period 7, and the third for the stands planted in period 7 and not harvested till the end of the planning horizon. Generalizing, in the formulation of Model II, there are four different kinds of decision variables. The first two kinds represent harvest opportunities during the planning horizon: on one side, for initially existing stands, and on the other side, for stands planted or created during the planning horizon. The last two kinds of variables account for no-harvest, again, of initially existing stands on one side and of stands created during the planning horizon on the other side.

As in the Model I formulation, the desirability of choices is evaluated through discounted cash flow indicators. But the computations must be done in a different way just to properly impute income and expenses to the right kind of decision variable. For example, for all variables representing the harvest opportunities of initially existing stands, only the present value of harvest income has to be computed. On the other side, all variables representing regeneration and harvest during the planning period must contain planting expenses along with harvest incomes, of course, properly discounted. Finally, for both no-harvest families of variables, the *terminal value* ($TV$) developed and presented in the Model I formulation must be enclosed and discounted, along with planting expenses only in the case of stands created during the planning horizon. It is through this terminal value that the bare land value ($BLV$) and the optimal economic rotation ($OER$) also participate in this formulation. In this notebook, the conceptual presentation of $TV$, $BLV$, and $OER$ will not be repeated, so it is advisable to either review Clutter et al. (1983) or Model I implementation (Yapura, 2024).

The Model II linear programming formulation for the XYZ Timber Co. problem can now be completed. The equation for the objective function is:

$$Q = \sum_{i=1}^N \sum_{j=1}^p D_{ij} Y_{ij} + \sum_{j=1}^{p-mha} \sum_{k=j+mha}^p E_{jk} X_{jk} + \sum_{i=1}^N T_i W_i + \sum_{j=1}^p Z_j U_j \qquad(1),$$

where $Q$ is to be maximized and denotes the present value of all future cash flows that will be produced by the managed forest; $Y_{ij}$ is the area of the initial stratum $i$ to be assigned to harvest in cutting period $j$, $D_{ij}$ is the per-unit area present value of all costs and incomes resulting from the assignment of the initial stratum $i$ to harvest in cutting period $j$, and $N$ and $p$ are the number of initial strata in the forest management unit and the number of cutting periods of the planning horizon, respectively; $X_{jk}$ is the area to be assigned to regeneration in cutting period $j$ and harvest in cutting period $k$, $E_{jk}$ is the per-unit area present value of all costs and incomes resulting from regeneration planting in cutting period $j$ and harvesting in cutting period $k$, and $mha$ is the minimum harvest age; $W_i$ is the area of the initial stratum $i$ to be left unharvested until the end of the planning horizon, and $T_i$ is the per-unit area present value of leaving the initial stratum $i$ unharvested through the whole planning horizon; and finally, $U_j$ is the area planted in period $j$ and left unharvested till the end of the planning horizon, and $Z_j$ is the per-unit area present value of regenerating in period $j$ and not harvesting till the end of the planning horizon.

In the Model II formulation, there are two kinds of area constraints. The first one is to ensure that the total area of each initial stratum is split into all feasible harvest opportunities during the planning horizon and the no-harvest option till the end of it:

$$\sum_{j=1}^p Y_{ij} + W_i = A_i \quad(i=1, 2,\dots, N) \qquad(2),$$

where $A_i$ is the available area in the initial stratum $i$.

The second kind of area constraints are the so-called transfer equations, which equate areas regenerated in the same period, on the left-hand side, with areas harvested in the same period:

$$\sum_{k=j+mha}^p X_{jk} + U_j = \sum_{i=1}^N Y_{ij} + \sum_{m=1}^{j-mha} G_{mj} X_{mj} \quad(j=1, 2,\dots, p) \qquad(3),$$

where $G_{mj} = 1$ indicates that areas regenerated in period $m$ and harvested in period $j$, denoted by $X_{mj}$, must be accounted for; otherwise, if $j < m + mha$, then $G_{mj} = 0$. Two important caveats are in order here: First, equation (3) is different from its counterpart labeled as (10.29) in Clutter et al. (1983, p. 300). More precisely, equation (3) includes a second term on the right-hand side that is improperly omitted in Clutter's counterpart. Second, $G_{mj}$ should not be regarded as indicator variables but indicator constants, and the not-so-elegant mathematical notation used was preferred for consistency with the notation used in the next equation, as it was preserved identical to the one used in Clutter et al. (1983).

To complete, the minimum harvest volume constraints ensure the required temporal pattern for committed volumes:

$$\sum_{i=1}^N V_{ij} Y_{ij} + \sum_{m=1}^{j-mha} H_{mj} X_{mj} \geqslant VMIN_j \quad(j=1, 2,\dots, p) \qquad(4),$$

where $H_{mj}$ is the per-unit area volume harvested in period $j$ from stands planted in $m$; otherwise, if $j < m + mha$, then $H_{mj} = 0$. Finally, $VMIN_j$ is the minimum allowed harvest volume in time period $j$.

---
## Gurobi Python implementation

Once again, installing the gurobipy package and importing the Gurobi Python Module is the first thing to do. In this notebook, no other Python convenience libraries were used. The Gurobi package includes a limited trial license that allows runnig the notebook online.

In [1]:
%pip install gurobipy
#import numpy as np
import gurobipy as gp
from gurobipy import GRB

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.4/13.4 MB 20.7 MB/s eta 0:00:00


All the data is collected in typical Python variables and data structures. It is worth mentioning that this notation is almost identical to the one used in Clutter et al. (1983). Also, the code is the same as in the Module I implementation (Yapura, 2024).

In [2]:
Y = {10: 29.10, 11: 34.98, 12: 40.80, 13: 46.67, 14: 52.22, 15: 57.00,
     16: 61.60, 17: 65.96, 18: 70.20, 19: 73.91, 20: 77.60, 21: 81.06,
     22: 84.26, 23: 87.40, 24: 90.24, 25: 92.75, 26: 94.90, 27: 96.93,
     28: 98.56, 29: 100.05, 30: 100.8} # Yield table: key is age, value is yield
Y[0] = 0 # For convenience
S = 25 # Stumpage price
R = 150 # Regeneration cost
T = 1.5 # Ad valorem tax and administrative costs
r = 0.05 # Interest rate
MHA = 10 # Minimum harvest age
n = 16 # Planning period
m = 2 # Cutting periods length
p = n // m # Number of cutting periods
N = 2 # Number of cutting units
M = 15 # Number of management regimes
mha = MHA // m # Minimum harvest age in periods

The calculation of the maximum $BLV$ and the age of the $OER$ is done with exactly the same code used in the Model I implementation (Yapura, 2024).

In [3]:
def blv(S, R, T, r, t):
    return (S * Y[t] - R) / ((1+r)**t - 1) - R - (T/r)

BLV_max = {t: blv(S, R, T, r, t) for t in Y if t > 0}
OER = max(BLV_max, key=BLV_max.get)
BLV_OER =  max(BLV_max.values())
print('OER =', OER, '- BLV_OER =', BLV_OER)

OER = 15 - BLV_OER = 1001.7283340357301


A regular Python dictionary is used to collect indices, as keys, for variables and coefficients related to areas of initially existing strata that are harvested during the planning horizon. Dictionary values are harvested volumes that are read from the yield table according to stand age and their present values, which are computed using necessary economic data.

In [4]:
coef_vol_pv_ij = {} # Initial strata harvested during planning horizon
init_age = {1: 13, 2: 0}
for i in range(1, N+1):
    for j in range(1, p+1):
        pv_cost_ij = 0 # Costs
        age_h = init_age[i] + j * m - m//2 if init_age[i] > 0 else 0
        pv_inco_ij = Y[age_h] * S / (1+r)**(j * m - m//2) # Incomes
        coef_vol_pv_ij[i, j] = Y[age_h], pv_inco_ij - pv_cost_ij
print(coef_vol_pv_ij)

{(1, 1): (52.22, 1243.3333333333333), (1, 2): (61.6, 1330.309901738473), (1, 3): (70.2, 1375.0884221521453), (1, 4): (77.6, 1378.7217804524353), (1, 5): (84.26, 1357.8686820127896), (1, 6): (90.24, 1319.0364761790024), (1, 7): (94.9, 1258.1874044059612), (1, 8): (98.56, 1185.22612969615), (2, 1): (0, 0.0), (2, 2): (0, 0.0), (2, 3): (0, 0.0), (2, 4): (0, 0.0), (2, 5): (0, 0.0), (2, 6): (0, 0.0), (2, 7): (0, 0.0), (2, 8): (0, 0.0)}


Another conceptually similar Python dictionary is used to collect indices, as keys, for variables and coefficients related to areas planted during the planning horizon that are also harvested during the planning horizon. Like before, dictionary values are harvested volumes that are read from the yield table according to stand age and their present values, which are computed using necessary economic data.

In [5]:
coef_vol_pv_jk = {} # Planted & harvested during planning horizon
for j in range(1, p-mha+1):
    for k in range(j+mha, p+1):
        pv_cost_jk = R / (1+r)**(j * m - m//2) # Costs
        pv_inco_jk = Y[(k-j)*m] * S / (1+r)**(k * m - m//2) # Incomes
        coef_vol_pv_jk[j, k] = Y[(k-j)*m], pv_inco_jk - pv_cost_jk
print(coef_vol_pv_jk)

{(1, 6): (29.1, 282.49703995324023), (1, 7): (40.8, 398.0706348010574), (1, 8): (52.22, 485.11067870061845), (2, 7): (29.1, 256.2331428147303), (2, 8): (40.8, 361.0618002730679), (3, 8): (29.1, 232.41101389091187)}


Now, a third regular Python dictionary is used to collect indices, as keys, for variables and coefficients related to areas of initially existing strata that remain unharvested until the end of the planning horizon. As there is no harvest, only the present values need to be computed and stored as dictionary values.

In [6]:
coef_pv_uh_i = {} # Initial strata, Unharvested
for i in range(1, N+1):
    age_f = init_age[i] + n if init_age[i] > 0 else 0 # age_f = A_k in model i formulation
    a_k = OER - age_f if age_f < OER else 0
    if age_f == 0: # Special case for brushlands & do nothing mr
        Y_t = 0; a_k = 0
    else:
        Y_t = Y[OER] if age_f <= OER else Y[age_f]
    coef_pv_uh_i[i] = ((Y_t * S + BLV_OER + (T/r)) / (1 + r)**a_k) / (1+r)**n
print(coef_pv_uh_i)

{1: 1618.4980817677492, 2: 472.6466373867599}


Finally, a fourth dictionary, conceptually similar to the third, is used to collect indices, as keys, for variables and coefficients related to areas planted during the planning horizon that remain unharvested until the end of the planning horizon. As before, just the present values need to be computed and stored as dictionary values.

In [7]:
coef_pv_uh_j = {} # Planted in j, Unharvested
for j in range(1, p+1):
    age_f = (p - j) * m +  m//2 # age_f = A_k in model i formulation
    a_k = OER - age_f if age_f < OER else 0
    Y_t = Y[OER] if age_f <= OER else Y[age_f]
    pv_cost_j = R / (1+r)**(j * m - m//2) # Costs
    tv_j = ((Y_t * S + BLV_OER + (T/r)) / (1 + r)**a_k) / (1+r)**n
    coef_pv_uh_j[j] = tv_j - pv_cost_j
print(coef_pv_uh_j)

{1: 982.5984133673619, 2: 891.2457264103056, 3: 808.3861464039053, 4: 733.2300647654469, 5: 665.0612832339654, 6: 603.2301888743449, 7: 547.1475636048481, 8: 496.2789692560978}


Now, all generated dictionaries are passed through the multidict() function, just to get the tupledicts that will provide tuplelist functionality to build indexed linear expressions.

In [8]:
ip_jh, vol_ij, pv_ij = gp.multidict(coef_vol_pv_ij)
jp_kh, vol_jk, pv_jk = gp.multidict(coef_vol_pv_jk)
ip_uh, pv_uh_i = gp.multidict(coef_pv_uh_i)
jp_uh, pv_uh_j = gp.multidict(coef_pv_uh_j)

Two final lines of code are necessary to gather two important pieces of data that were not hardcoded before, and then the optimization model itself can be deployed. Equations (1) to (4) were coded using standard gurobipy constructs. It is worth noting that the not-so-elegant mathematical notation presented in equations (3) and (4) can be done in a remarkable natural and clear way with gurobypy constructs for dealing with indices. And there was no need to code unusual indicator constants. To conclude, the same practical approach for imputation of ad valorem tax and administrative costs used in the Model I implementation was reproduced here. Then, the present value of all future tax and administrative costs, properly affected by the total area of the forest management unit, was computed only once and then subtracted from the objective value of the optimum solution. This corrected value, as well as the optimal assignment of areas and the left-hand side (LHS) of all constraints, are printed in the end.

In [10]:
A = {1: 90000, 2: 65000} # Initial areas of cutting units
VMIN = 1e6 # Minimum periodic harvest volume

with gp.Model("Model II") as model:
    Y = model.addVars(ip_jh, name="Y")
    X = model.addVars(jp_kh, name="X")
    W = model.addVars(ip_uh, name="W")
    U = model.addVars(jp_uh, name="U")

    # Equation (2)
    model.addConstrs((Y.sum(i, '*') + W[i] ==
                      A[i] for i in range(1, N+1)),
                     name="initial_area")

    # Equation (3)
    model.addConstrs((X.sum(j, '*') + U[j] ==
                      Y.sum('*', j) + X.sum('*', j) for j in range(1, p+1)),
                     name="transfer_area")

    # Equation (4)
    model.addConstrs((Y.prod(vol_ij, '*', j) + X.prod(vol_jk, '*', j) >=
                      VMIN for j in range(1, p+1)),
                     name="periodic_harvest")

    # Equation (1)
    linexpr = Y.prod(pv_ij) + X.prod(pv_jk) + \
              W.prod(pv_uh_i) + U.prod(coef_pv_uh_j)
    model.setObjective(linexpr, GRB.MAXIMIZE)

    model.write("model_ii.lp")

    model.optimize()

    if model.status == GRB.OPTIMAL:
        print('\n****************** SOLUTION ******************')
        print(f'\tStatus       : {model.Status}')
        print(f'\tObj          : {model.ObjVal}')
        PV_T = sum(A.values()) * T / r
        print(f'\n\tPresent value of the forest: {model.ObjVal - PV_T:.0f}')
        print(f'\n\tDecision variable values:')
        for var in model.getVars():
            print(f'\t{var.VarName} = {var.X:.0f}')
        print('\n\tArea and volume constraints:')
        for constraints in model.getConstrs():
            LHS = constraints.rhs - constraints.slack
            print(f'\t{constraints.ConstrName} LHS = {LHS:.0f}')

Gurobi Optimizer version 11.0.2 build v11.0.2rc0 (linux64 - "Ubuntu 22.04.3 LTS")

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Optimize a model with 18 rows, 32 columns and 68 nonzeros
Model fingerprint: 0x5312ef2a
Coefficient statistics:
  Matrix range     [1e+00, 1e+02]
  Objective range  [2e+02, 2e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [6e+04, 1e+06]
Presolve removed 10 rows and 14 columns
Presolve time: 0.01s
Presolved: 8 rows, 18 columns, 33 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    9.1858607e+08   1.838771e+05   0.000000e+00      0s
       8    2.5538063e+08   0.000000e+00   0.000000e+00      0s

Solved in 8 iterations and 0.02 seconds (0.00 work units)
Optimal objective  2.553806302e+08

****************** SOLUTION ******************
	Status       : 2
	Obj          : 255380630.20257273

	Present value of the fo

---
## References

Clutter, J. L., Fortson, J. C., Pienaar, L. V., Brister G. H. & Bailey, R. L. (1983). Timber management: a quantitative approach. John Wiley & Sons.

Johnson, K. N. & Scheurman, H. L. (1977). Techniques for prescribing optimal harvest and investment under different objectives: discussion and synthesis. Forest Science 23, Issue suppl_1 (Forest Science Monograph 18).

Yapura, P. (2024). Forest harvest scheduling with Model I linear programming formulation: a Gurobi Python implementation [Google Colab Jupyter Notebook]. http://sedici.unlp.edu.ar/handle/10915/163465

---
This notebook was developed only for instructional purposes. Feedback, suggestions, and error reports are welcome. Please e-mail to ypf@agro.unlp.edu.ar.

[Forest harvest scheduling with Model II linear programming formulation: a Gurobi Python implementation](https://colab.research.google.com/drive/1LkwMasfDfjJv6WmgmjH6MCIYsbnp6ZVS?usp=sharing) © 2024 by Pablo Yapura is licensed under Creative Commons [Attribution-ShareAlike 4.0 International](https://creativecommons.org/licenses/by-sa/4.0/?ref=chooser-v1).